In [52]:
import MySQLdb
import pandas
import itertools
import numpy as np
# import bm25fe
import pickle

In [53]:
conn = MySQLdb.connect(host='10.117.8.41', port=3306, user='root', passwd='vmware', db='bugfeature')
cur = conn.cursor()

sql = '''SELECT bug_id, short_desc, long_desc
FROM bugs_cpdplatform'''

# bugs = pandas.io.sql.read_sql(sql, conn).set_index(['bug_id'])
bugs = pandas.io.sql.read_sql(sql, conn)

In [54]:
with open('bugset.txt', 'rb') as f:
    bugset = pickle.load(f)
    
criterion = bugs['bug_id'].map(lambda x: x in bugset)
bugs_train = bugs[criterion]
n = bugs_train.shape[0]

texts = list((bugs_train['short_desc'] +' '+ bugs_train['long_desc']).map(lambda x: x.split()))

In [55]:
# with open('train100.txt', 'rb') as f:
#    train = pickle.load(f)

# bugset = []
# for item in train:
#     bugset.append(item['query'])
#     bugset.append(item['rel'])
#     bugset += item['irrel']

# bugset = set(bugset)

# criterion = bugs['bug_id'].map(lambda x: x in bugset)
# bugs_train = bugs[criterion]
# n = bugs_train.shape[0]
# texts = list((bugs_train['short_desc'] +' '+ bugs_train['long_desc']).map(lambda x: x.split()))

In [56]:
# print n
# print len(texts)
# print len(bugset)
# print train
# print bugs_filtered.shape
# print criterion
# print bugset
# print bugs.shape
# print type(criterion1)

In [57]:
from gensim import corpora

dictionary = corpora.Dictionary(list(bugs_train['long_desc'].map(lambda x: x.split())))
dictionary.filter_extremes(no_below = 10, no_above = 0.9, keep_n = 100000)
dictionary.add_documents(list(bugs_train['short_desc'].map(lambda x: x.split())))

dictionary.save_as_text('dictionary.txt')

corpus = [dictionary.doc2bow(text) for text in texts]

In [58]:
from gensim.models import hdpmodel
hdp = hdpmodel.HdpModel(corpus, id2word=dictionary)
hdp.save('hdpmodel.txt')

In [60]:
from gensim.models import ldamulticore
lda = ldamulticore.LdaMulticore(corpus, id2word=dictionary, iterations=10000)
lda.save('ldamodel.txt')

In [49]:
print dictionary.dfs
print dictionary.dfs.values()

{0: 30, 1: 78, 2: 82, 3: 33, 4: 16, 5: 11, 6: 87, 7: 179, 8: 247, 9: 15, 10: 54, 11: 338, 12: 14, 13: 12, 14: 14, 15: 20, 16: 10, 17: 18, 18: 53, 19: 51, 20: 43, 21: 26, 22: 22, 23: 12, 24: 630, 25: 138, 26: 10, 27: 55, 28: 24, 29: 12, 30: 14, 31: 171, 32: 17, 33: 24, 34: 52, 35: 18, 36: 13, 37: 589, 38: 33, 39: 16, 40: 17, 41: 149, 42: 40, 43: 23, 44: 48, 45: 13, 46: 28, 47: 15, 48: 24, 49: 23, 50: 20, 51: 20, 52: 47, 53: 12, 54: 23, 55: 12, 56: 21, 57: 204, 58: 927, 59: 36, 60: 10, 61: 64, 62: 28, 63: 1018, 64: 46, 65: 1460, 66: 17, 67: 26, 68: 13, 69: 13, 70: 18, 71: 39, 72: 41, 73: 1104, 74: 19, 75: 544, 76: 17, 77: 13, 78: 34, 79: 10, 80: 27, 81: 18, 82: 14, 83: 37, 84: 22, 85: 13, 86: 45, 87: 43, 88: 16, 89: 32, 90: 10, 91: 48, 92: 38, 93: 976, 94: 10, 95: 34, 96: 73, 97: 12, 98: 221, 99: 10, 100: 27, 101: 350, 102: 274, 103: 13, 104: 107, 105: 40, 106: 138, 107: 16, 108: 17, 109: 22, 110: 131, 111: 16, 112: 568, 113: 16, 114: 10, 115: 13, 116: 10, 117: 133, 118: 10, 119: 15, 120

In [50]:
distribution = hdp.inference(corpus)

[[  1.31694530e+03   2.17358126e-01   1.65997172e-01 ...,   1.02282953e-06
    5.74969871e-07   6.51773433e-07]
 [  5.49711122e+02   5.87393640e+02   1.66229214e-01 ...,   1.02282953e-06
    5.74969871e-07   6.51773433e-07]
 [  7.81174229e+00   2.19165638e-01   1.66185555e-01 ...,   1.02282953e-06
    5.74969871e-07   6.51773433e-07]
 ..., 
 [  6.92305469e+02   2.15458782e-01   1.65779793e-01 ...,   1.02282953e-06
    5.74969871e-07   6.51773433e-07]
 [  4.34931387e+01   2.19077434e-01   1.69520705e-01 ...,   1.02282953e-06
    5.74969871e-07   6.51773433e-07]
 [  1.05373366e+00   8.09802077e+01   9.08477955e+01 ...,   1.02282953e-06
    5.74969871e-07   6.51773433e-07]]


In [ ]:
for item in distribution:
    print item

[  1.31694530e+03   2.17358126e-01   1.65997172e-01   2.05842373e-02
   1.07994988e-02   2.18250174e-02   4.68243964e-03   5.48950111e-03
   2.41039982e-03   2.80874735e-03   6.97406450e-04   1.24233926e-03
   2.08809761e-03   1.00755504e+03   2.36690857e-03   1.68027648e-03
   1.97971395e-03   1.13765896e-03   1.42549712e-03   1.08700896e-03
   7.00274028e-04   1.60941126e-03   9.24683475e-04   8.54185528e-04
   1.41892451e-03   8.33121175e-04   3.97474196e-04   9.88858724e-04
   8.90132448e-04   2.33385073e-03   7.19955686e-04   4.08519567e-04
   1.08167622e-03   4.85081007e-04   5.94416350e-04   1.24779900e-03
   7.52063568e-04   6.32651004e-04   3.84426708e-04   5.03755200e-04
   3.61764737e-04   3.63638162e-04   3.66879372e-04   4.55842762e-04
   7.31830554e-04   3.46082459e-04   6.70873152e-04   1.44265501e-03
   3.76640195e-04   1.33561914e-04   1.24333878e-04   3.41531427e-04
   3.71870494e-04   3.46644058e-04   3.81249937e-04   1.86686728e-04
   4.07111758e-04   9.24678838e-05